# Import Modules

In [1]:
import numpy as np
from fourrooms import Fourrooms
from IPython.display import clear_output
from aoaoc_tabular import *
import matplotlib.pyplot as plt
from visualize import Visualization

# HyperParameters

In [2]:
# Replace the command line argparse
class Arguments:
    def __init__(self):
        # Numbers
        self.nepisodes=3000
        self.nsteps=2000
        self.noptions=2
        
        # Learning Rates
        self.lr_term=0.25
        self.lr_intra=0.25
        self.lr_critic=0.5
        self.lr_criticA=0.5
        self.lr_attend=0.01
        
        # Environment Parameters
        self.discount=0.99
        self.deterministic = False
        self.punishEachStep = True
        self.modified = False
        self.easier = False
        
        self.goalChangeEps = 5000
        
        # Attention Parameters
        self.h_learn = True
        self.normalize = True
               
        # Policy Parameters
        self.epsilon=1e-1
        self.temp=2.
        
        # Objective Parameters
        self.wo1 = 0.1   #q
        self.wo2 = 1.    #cosim
        self.wo3 = 0.    #entropy
        self.wo4 = 0.    #size
        
        # Randomness Parameters
        self.seed=2222
        self.seed_startstate=1111
        
        # Display Parameters
        self.showMap = False
        self.showAttention = False
        self.showOptPref = False
        self.showFrequency = 10
        
        # Other Parameters
        self.baseline=True
        self.dc = 2.
        
        
args = Arguments()

In [3]:
woList = [0.01, 0.05, 0.1, 0.2]
dcList = [1,2,3]
mixedList = []
for i in woList:
    for j in dcList:
        mixedList.append([i,j])

# Run

## Set up

In [4]:
rng = np.random.RandomState(args.seed)
env = Fourrooms(args.seed_startstate, args.punishEachStep, args.deterministic, args.modified, args.easier)

possible_next_goals = [68, 69, 70, 71, 72, 78, 79, 80, 81, 82, 88, 89, 90, 91, 92, 93, 99, 100, 101, 102, 103]

features = Tabular(env.observation_space)
nfeatures, nactions = len(features), env.action_space

viz = Visualization(env, args, nactions)

cumRewRec = np.zeros(args.nepisodes)
stepRec = np.zeros(args.nepisodes)

## Main loop

In [ ]:
# Set up classes
policy_over_options = POO(rng, nfeatures, args)
CoSimObj.reset()
options = [Option(rng, nfeatures, nactions, args, policy_over_options, i) for i in range(args.noptions)]

# Loop through games
for episode in range(args.nepisodes):
    # Goal Change
    if episode == args.goalChangeEps:
#         env.goal = int(np.random.uniform(0, env.observation_space))
        env = Fourrooms(args.seed_startstate, args.punishEachStep, args.deterministic, args.modified, False)
        viz = Visualization(env, args, nactions)
    
    # Initial state
    return_per_episode = 0.0
    observation = env.reset()
    phi = features(observation)    
    option = policy_over_options.sample(phi)
    action = options[option].sample(phi)
    traject = [[phi,option],[phi,option],action]
    viz.resetMap(phi)

    # Reset record
    cumreward = 0.
    duration = 1
    option_switches = 0
    avgduration = 0.

    # Loop through frames in 1 game
    for step in range(args.nsteps):
        # Collect feedback from environment
        observation, reward, done, _ = env.step(action)
        phi = features(observation)
        return_per_episode += pow(args.discount,step)*reward

        # Render
        if args.showMap and episode % 100 == 99:
            clear_output(wait=True)
            viz.showMap(phi, option)

        # Store option index
        last_option = option

        # Check termination
        termination = options[option].terminate(phi, value=True)
        if options[option].terminate(phi):
            option = policy_over_options.sample(phi)
            option_switches += 1
            avgduration += (1./option_switches)*(duration - avgduration)
            duration = 1

        # Record into trajectory
        traject[0] = traject[1]
        traject[1] = [phi, option]
        traject[2] = action

        # Sample next action
        action = options[option].sample(phi)

        # Policy Evaluation + Policy Improvement
        baseline = policy_over_options.value(traject[0][0], traject[0][1])
        advantage = policy_over_options.advantage(phi, last_option)
        options[last_option].update(traject, reward, done, phi, last_option, termination, baseline, advantage)
        policy_over_options.update(traject, reward, done, termination)

        # End of frame
        cumreward += reward
        duration += 1
        if done:
            break

    # Attention graph
    if episode % args.showFrequency == 0:
        if args.showAttention:
            clear_output(wait=True)
            viz.showAttention(options)
            print(options[0].policy.attention.weights)
        if args.showOptPref:
            clear_output(wait=True)
            viz.showPref(policy_over_options.weights)
    cumRewRec[episode] = cumreward
    stepRec[episode] = step
    print('Episode {} steps {} cumreward {} avg. duration {} switches {}'.format(episode, step, cumreward, avgduration, option_switches))

In [ ]:
for c in mixedList:
    args.lr_attend = c[0]
    args.dc = c[1]
    for r in range(5):
        # Set up classes
        policy_over_options = POO(rng, nfeatures, args)
        CoSimObj.reset()
        options = [Option(rng, nfeatures, nactions, args, policy_over_options, i) for i in range(args.noptions)]

        # Loop through games
        for episode in range(args.nepisodes):
            # Goal Change
            if episode == args.goalChangeEps:
        #         env.goal = int(np.random.uniform(0, env.observation_space))
                env = Fourrooms(args.seed_startstate, args.punishEachStep, args.deterministic, args.modified, False)
                viz = Visualization(env, args, nactions)

            # Initial state
            return_per_episode = 0.0
            observation = env.reset()
            phi = features(observation)    
            option = policy_over_options.sample(phi)
            action = options[option].sample(phi)
            traject = [[phi,option],[phi,option],action]
            viz.resetMap(phi)

            # Reset record
            cumreward = 0.
            duration = 1
            option_switches = 0
            avgduration = 0.

            # Loop through frames in 1 game
            for step in range(args.nsteps):
                # Collect feedback from environment
                observation, reward, done, _ = env.step(action)
                phi = features(observation)
                return_per_episode += pow(args.discount,step)*reward

                # Render
                if args.showMap and episode % 100 == 99:
                    clear_output(wait=True)
                    viz.showMap(phi, option)

                # Store option index
                last_option = option

                # Check termination
                termination = options[option].terminate(phi, value=True)
                if options[option].terminate(phi):
                    option = policy_over_options.sample(phi)
                    option_switches += 1
                    avgduration += (1./option_switches)*(duration - avgduration)
                    duration = 1

                # Record into trajectory
                traject[0] = traject[1]
                traject[1] = [phi, option]
                traject[2] = action

                # Sample next action
                action = options[option].sample(phi)

                # Policy Evaluation + Policy Improvement
                baseline = policy_over_options.value(traject[0][0], traject[0][1])
                advantage = policy_over_options.advantage(phi, last_option)
                options[last_option].update(traject, reward, done, phi, last_option, termination, baseline, advantage)
                policy_over_options.update(traject, reward, done, termination)

                # End of frame
                cumreward += reward
                duration += 1
                if done:
                    break

            # Attention graph
            if episode % args.showFrequency == 0:
                if args.showAttention:
                    clear_output(wait=True)
                    viz.showAttention(options)
                    print(options[0].policy.attention.weights)
                if args.showOptPref:
                    clear_output(wait=True)
                    viz.showPref(policy_over_options.weights)
            cumRewRec[episode] = cumreward
            stepRec[episode] = step
            print('Episode {} steps {} cumreward {} avg. duration {} switches {}'.format(episode, step, cumreward, avgduration, option_switches))
        viz.savePref(policy_over_options.weights, "aoaoc", c[0], c[1], r)

Episode 0 steps 324 cumreward -598.0 avg. duration 3.20408163265306 switches 147
Episode 1 steps 10 cumreward 30.0 avg. duration 3.0 switches 5
Episode 2 steps 181 cumreward -312.0 avg. duration 2.9042553191489358 switches 94
Episode 3 steps 364 cumreward -678.0 avg. duration 2.9890710382513643 switches 183
Episode 4 steps 936 cumreward -1822.0 avg. duration 3.2885085574572126 switches 409
Episode 5 steps 39 cumreward -28.0 avg. duration 3.2941176470588234 switches 17
Episode 6 steps 8 cumreward 34.0 avg. duration 2.1428571428571432 switches 7
Episode 7 steps 77 cumreward -104.0 avg. duration 3.5666666666666664 switches 30
Episode 8 steps 14 cumreward 22.0 avg. duration 2.5555555555555554 switches 9
Episode 9 steps 73 cumreward -96.0 avg. duration 3.147058823529412 switches 34
Episode 10 steps 448 cumreward -846.0 avg. duration 3.4585635359116016 switches 181
Episode 11 steps 80 cumreward -110.0 avg. duration 3.6333333333333337 switches 30
Episode 12 steps 16 cumreward 18.0 avg. durati

Episode 112 steps 31 cumreward -12.0 avg. duration 3.142857142857143 switches 14
Episode 113 steps 14 cumreward 22.0 avg. duration 2.6250000000000004 switches 8
Episode 114 steps 17 cumreward 16.0 avg. duration 3.0 switches 8
Episode 115 steps 16 cumreward 18.0 avg. duration 3.5 switches 6
Episode 116 steps 16 cumreward 18.0 avg. duration 3.142857142857143 switches 7
Episode 117 steps 19 cumreward 12.0 avg. duration 2.5 switches 12
Episode 118 steps 11 cumreward 28.0 avg. duration 4.333333333333333 switches 3
Episode 119 steps 5 cumreward 40.0 avg. duration 2.0 switches 4
Episode 120 steps 15 cumreward 20.0 avg. duration 3.3333333333333335 switches 6
Episode 121 steps 11 cumreward 28.0 avg. duration 2.4285714285714284 switches 7
Episode 122 steps 12 cumreward 26.0 avg. duration 3.7500000000000004 switches 4
Episode 123 steps 38 cumreward -26.0 avg. duration 3.846153846153846 switches 13
Episode 124 steps 5 cumreward 40.0 avg. duration 2.3333333333333335 switches 3
Episode 125 steps 24 

Episode 227 steps 16 cumreward 18.0 avg. duration 3.5 switches 6
Episode 228 steps 22 cumreward 6.0 avg. duration 3.625 switches 8
Episode 229 steps 8 cumreward 34.0 avg. duration 3.3333333333333335 switches 3
Episode 230 steps 19 cumreward 12.0 avg. duration 2.5 switches 12
Episode 231 steps 10 cumreward 30.0 avg. duration 2.2857142857142856 switches 7
Episode 232 steps 14 cumreward 22.0 avg. duration 3.1666666666666665 switches 6
Episode 233 steps 7 cumreward 36.0 avg. duration 4.0 switches 2
Episode 234 steps 21 cumreward 8.0 avg. duration 2.5384615384615388 switches 13
Episode 235 steps 16 cumreward 18.0 avg. duration 2.875 switches 8
Episode 236 steps 11 cumreward 28.0 avg. duration 3.0 switches 5
Episode 237 steps 3 cumreward 44.0 avg. duration 1.6666666666666667 switches 3
Episode 238 steps 14 cumreward 22.0 avg. duration 3.1666666666666665 switches 6
Episode 239 steps 32 cumreward -14.0 avg. duration 3.583333333333333 switches 12
Episode 240 steps 29 cumreward -8.0 avg. duratio

Episode 346 steps 4 cumreward 42.0 avg. duration 4.0 switches 1
Episode 347 steps 5 cumreward 40.0 avg. duration 2.3333333333333335 switches 3
Episode 348 steps 4 cumreward 42.0 avg. duration 2.5 switches 2
Episode 349 steps 24 cumreward 2.0 avg. duration 4.285714285714286 switches 7
Episode 350 steps 6 cumreward 38.0 avg. duration 2.6666666666666665 switches 3
Episode 351 steps 1 cumreward 48.0 avg. duration 1.0 switches 1
Episode 352 steps 12 cumreward 26.0 avg. duration 4.666666666666667 switches 3
Episode 353 steps 13 cumreward 24.0 avg. duration 3.4 switches 5
Episode 354 steps 27 cumreward -4.0 avg. duration 3.888888888888889 switches 9
Episode 355 steps 27 cumreward -4.0 avg. duration 2.3000000000000007 switches 20
Episode 356 steps 22 cumreward 6.0 avg. duration 4.0 switches 7
Episode 357 steps 4 cumreward 42.0 avg. duration 2.5 switches 2
Episode 358 steps 20 cumreward 10.0 avg. duration 2.0555555555555554 switches 18
Episode 359 steps 33 cumreward -16.0 avg. duration 3.0 swit

Episode 463 steps 10 cumreward 30.0 avg. duration 5.5 switches 2
Episode 464 steps 9 cumreward 32.0 avg. duration 5.0 switches 2
Episode 465 steps 19 cumreward 12.0 avg. duration 2.4999999999999996 switches 12
Episode 466 steps 15 cumreward 20.0 avg. duration 3.8 switches 5
Episode 467 steps 20 cumreward 10.0 avg. duration 3.5714285714285716 switches 7
Episode 468 steps 1 cumreward 48.0 avg. duration 1.0 switches 1
Episode 469 steps 17 cumreward 16.0 avg. duration 4.2 switches 5
Episode 470 steps 22 cumreward 6.0 avg. duration 3.3333333333333335 switches 9
Episode 471 steps 5 cumreward 40.0 avg. duration 4.0 switches 1
Episode 472 steps 12 cumreward 26.0 avg. duration 2.8333333333333335 switches 6
Episode 473 steps 9 cumreward 32.0 avg. duration 2.0 switches 8
Episode 474 steps 6 cumreward 38.0 avg. duration 2.25 switches 4
Episode 475 steps 0 cumreward 50.0 avg. duration 0.0 switches 0
Episode 476 steps 2 cumreward 46.0 avg. duration 1.5 switches 2
Episode 477 steps 4 cumreward 42.0 a

...

Episode 1209 steps 32 cumreward -14.0 avg. duration 32.0 switches 1
Episode 1210 steps 2 cumreward 46.0 avg. duration 1.0 switches 1
Episode 1211 steps 13 cumreward 24.0 avg. duration 2.8333333333333335 switches 6
Episode 1212 steps 15 cumreward 20.0 avg. duration 2.4000000000000004 switches 10
Episode 1213 steps 17 cumreward 16.0 avg. duration 2.5555555555555554 switches 9
Episode 1214 steps 3 cumreward 44.0 avg. duration 1.0 switches 1
Episode 1215 steps 0 cumreward 50.0 avg. duration 0.0 switches 0
Episode 1216 steps 14 cumreward 22.0 avg. duration 5.333333333333333 switches 3
Episode 1217 steps 11 cumreward 28.0 avg. duration 2.3333333333333335 switches 6
Episode 1218 steps 8 cumreward 34.0 avg. duration 8.0 switches 1
Episode 1219 steps 15 cumreward 20.0 avg. duration 2.6 switches 5
Episode 1220 steps 5 cumreward 40.0 avg. duration 2.0 switches 3
Episode 1221 steps 20 cumreward 10.0 avg. duration 6.666666666666667 switches 3
Episode 1222 steps 9 cumreward 32.0 avg. duration 0.0 sw

Episode 1327 steps 17 cumreward 16.0 avg. duration 9.0 switches 2
Episode 1328 steps 1 cumreward 48.0 avg. duration 0.0 switches 0
Episode 1329 steps 10 cumreward 30.0 avg. duration 10.0 switches 1
Episode 1330 steps 19 cumreward 12.0 avg. duration 4.0 switches 6
Episode 1331 steps 21 cumreward 8.0 avg. duration 4.333333333333333 switches 6
Episode 1332 steps 10 cumreward 30.0 avg. duration 2.0 switches 7
Episode 1333 steps 9 cumreward 32.0 avg. duration 2.2 switches 5
Episode 1334 steps 6 cumreward 38.0 avg. duration 6.0 switches 1
Episode 1335 steps 13 cumreward 24.0 avg. duration 4.0 switches 4
Episode 1336 steps 29 cumreward -8.0 avg. duration 4.374999999999999 switches 8
Episode 1337 steps 17 cumreward 16.0 avg. duration 3.5 switches 6
Episode 1338 steps 2 cumreward 46.0 avg. duration 1.5 switches 2
Episode 1339 steps 8 cumreward 34.0 avg. duration 1.6666666666666667 switches 3
Episode 1340 steps 4 cumreward 42.0 avg. duration 2.0 switches 1
Episode 1341 steps 18 cumreward 14.0 av

Episode 1448 steps 13 cumreward 24.0 avg. duration 3.0 switches 5
Episode 1449 steps 13 cumreward 24.0 avg. duration 5.0 switches 3
Episode 1450 steps 13 cumreward 24.0 avg. duration 6.0 switches 2
Episode 1451 steps 8 cumreward 34.0 avg. duration 3.5 switches 2
Episode 1452 steps 5 cumreward 40.0 avg. duration 2.3333333333333335 switches 3
Episode 1453 steps 17 cumreward 16.0 avg. duration 5.0 switches 4
Episode 1454 steps 9 cumreward 32.0 avg. duration 2.5 switches 4
Episode 1455 steps 12 cumreward 26.0 avg. duration 2.2857142857142856 switches 7
Episode 1456 steps 9 cumreward 32.0 avg. duration 2.6 switches 5
Episode 1457 steps 11 cumreward 28.0 avg. duration 5.0 switches 2
Episode 1458 steps 13 cumreward 24.0 avg. duration 3.4 switches 5
Episode 1459 steps 11 cumreward 28.0 avg. duration 11.0 switches 1
Episode 1460 steps 6 cumreward 38.0 avg. duration 2.0 switches 3
Episode 1461 steps 27 cumreward -4.0 avg. duration 3.3636363636363638 switches 11
Episode 1462 steps 11 cumreward 28

Episode 1570 steps 5 cumreward 40.0 avg. duration 2.0 switches 4
Episode 1571 steps 12 cumreward 26.0 avg. duration 4.666666666666666 switches 3
Episode 1572 steps 35 cumreward -20.0 avg. duration 4.3999999999999995 switches 10
Episode 1573 steps 12 cumreward 26.0 avg. duration 6.0 switches 2
Episode 1574 steps 0 cumreward 50.0 avg. duration 0.0 switches 0
Episode 1575 steps 28 cumreward -6.0 avg. duration 2.7857142857142856 switches 14
Episode 1576 steps 36 cumreward -22.0 avg. duration 4.5 switches 10
Episode 1577 steps 6 cumreward 38.0 avg. duration 2.0 switches 2
Episode 1578 steps 2 cumreward 46.0 avg. duration 2.0 switches 1
Episode 1579 steps 13 cumreward 24.0 avg. duration 3.0 switches 3
Episode 1580 steps 15 cumreward 20.0 avg. duration 4.25 switches 4
Episode 1581 steps 8 cumreward 34.0 avg. duration 2.166666666666667 switches 6
Episode 1582 steps 12 cumreward 26.0 avg. duration 3.0 switches 5
Episode 1583 steps 9 cumreward 32.0 avg. duration 2.75 switches 4
Episode 1584 step

Episode 1687 steps 22 cumreward 6.0 avg. duration 8.0 switches 3
Episode 1688 steps 17 cumreward 16.0 avg. duration 2.75 switches 8
Episode 1689 steps 17 cumreward 16.0 avg. duration 5.0 switches 4
Episode 1690 steps 14 cumreward 22.0 avg. duration 3.6 switches 5
Episode 1691 steps 10 cumreward 30.0 avg. duration 2.0 switches 5
Episode 1692 steps 13 cumreward 24.0 avg. duration 7.0 switches 2
Episode 1693 steps 16 cumreward 18.0 avg. duration 3.0 switches 7
Episode 1694 steps 22 cumreward 6.0 avg. duration 5.2 switches 5
Episode 1695 steps 17 cumreward 16.0 avg. duration 3.142857142857143 switches 7
Episode 1696 steps 24 cumreward 2.0 avg. duration 3.2 switches 10
Episode 1697 steps 27 cumreward -4.0 avg. duration 4.125 switches 8
Episode 1698 steps 14 cumreward 22.0 avg. duration 2.5714285714285716 switches 7
Episode 1699 steps 20 cumreward 10.0 avg. duration 4.4 switches 5
Episode 1700 steps 7 cumreward 36.0 avg. duration 7.0 switches 1
Episode 1701 steps 16 cumreward 18.0 avg. durat

# Visualization

## Simulate an episode

In [ ]:
states = np.zeros((13,13), dtype="int")
occupancy = env.occupancy.astype('float64')
s=0
for i in range(13):
    for j in range(13):
        if occupancy[i,j] == 0:
            states[i,j] = s
            s+=1
print(states)

In [ ]:
startState = 57
# Simulation
observation = env.reset(startState)
viz.resetMap(phi)

option = policy_over_options.sample(phi)
action = options[option].sample(phi)

for step in range(args.nsteps):
    observation, reward, done, _ = env.step(action)
    phi = features(observation)

    #render
    clear_output(wait=True)
    viz.showMap(phi, option)

    if options[option].terminate(phi):
        option = policy_over_options.sample(phi)

    action = options[option].sample(phi)

    if done:
        break

## Display action and option preference in each state

In [ ]:
# Display option preference
viz.showPref(policy_over_options.weights)

In [ ]:
opt = 0
# Display action preference for opt
viz.showPref(options[opt].weights)

## Display Attention

In [ ]:
viz.showAttention(options)

In [ ]:
plt.plot(cumRewRec)
plt.show()

In [ ]:
plt.plot(stepRec)
plt.show()

In [ ]:
options[0].policy.internalPI.weights[0]

In [ ]:
plt.plot(cumRewRec)
plt.show()

In [ ]:
plt.plot(stepRec)
plt.show()

In [ ]:
plt.plot(cumRewRec)
plt.show()